# Time series interpolating with aeon

Suppose we have a set of time series with different lengths, i.e. different number
of time points. Currently, most of aeon's functionality requires equal-length time series, so to use aeon, we need to first converted our data into equal-length time series. In this tutorial, you will learn how to use the `TSInterpolator` to do so.

In [1]:
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline

from aeon.classification.convolution_based import RocketClassifier
from aeon.datasets import load_basic_motions
from aeon.transformations.compose import ColumnConcatenator

## Ordinary situation

Here is a normal situation, when all time series have same length. We load an example
 data set from aeon and train a classifier.

In [2]:
X, y = load_basic_motions(return_type="nested_univ")
X_train, X_test, y_train, y_test = train_test_split(X, y)

steps = [
    ("concatenate", ColumnConcatenator()),
    ("classify", RocketClassifier()),
]
clf = Pipeline(steps)
clf.fit(X_train, y_train)
clf.score(X_test, y_test)

0.25

## If time series are unequal length, aeon's algorithm may raise an error

Now we are going to spoil the data set a little bit by randomly cutting the time series. This leads to unequal-length time series. Consequently, we have an error while attempt to train a classifier.

In [4]:
from aeon.datasets import load_plaid

X, y = load_plaid(return_type="nested_univ")
X_train, X_test, y_train, y_test = train_test_split(X, y)

try:
    clf = RocketClassifier()
    clf = Pipeline(steps)
    clf.fit(X_train, y_train)
    clf.score(X_test, y_test)
except ValueError as e:
    print(f"ValueError: {e}")

IndexError: Data seen by RocketClassifier instance has unequal length series, but this RocketClassifier instance cannot handle unequal length series. Calls with unequal length series may result in error or unreliable results.


# Now the interpolator enters
Now we use our interpolator to resize time series of different lengths to user-defined length. Internally, it uses linear interpolation from scipy and draws equidistant samples on the user-defined number of points.

After interpolating the data, the classifier works again.

In [5]:
from aeon.transformations.collection.interpolate import TSInterpolator

steps = [
    ("transform", TSInterpolator(50)),
    ("classify", RocketClassifier()),
]
clf = Pipeline(steps)
clf.fit(X_train, y_train)
clf.score(X_test, y_test)

0.7732342007434945